In [1]:
import requests
from bs4 import BeautifulSoup
import pandas as pd
from pprint import pprint

In [2]:
# 參數設定
year = 2025
quarter = 3
stockCode = '1101'

# 目標網址
url = f"https://mopsov.twse.com.tw/server-java/t164sb01?step=3&SYEAR={year}&file_name=tifrs-fr1-m1-ci-cr-{stockCode}-{year}Q{quarter}.html"

# 發送 GET 請求
response = requests.get(url)

# 確認回應成功
if response.status_code == 200:
    pprint(response.text)
else:
    print("錯誤，Status Code:", response.status_code)


('<html>\r\n'
 '<head>\r\n'
 "<META HTTP-EQUIV='Content-Type' CONTENT='text/html; charset=big5'>\r\n"
 '<?xml version="1.0" encoding="UTF-8"?> \r\n'
 '<html xmlns="http://www.w3.org/1999/xhtml"\r\n'
 'xmlns:ifrs-full="http://xbrl.ifrs.org/taxonomy/2017-03-09/ifrs-full"\r\n'
 'xmlns:iso4217="http://www.xbrl.org/2003/iso4217"\r\n'
 'xmlns:link="http://www.xbrl.org/2003/linkbase"\r\n'
 'xmlns:xbrldi="http://xbrl.org/2006/xbrldi"\r\n'
 'xmlns:xbrldt="http://xbrl.org/2005/xbrldt"\r\n'
 'xmlns:xbrli="http://www.xbrl.org/2003/instance"\r\n'
 'xmlns:xlink="http://www.w3.org/1999/xlink"\r\n'
 'xmlns:ix="http://www.xbrl.org/2013/inlineXBRL"\r\n'
 'xmlns:ixt="http://www.xbrl.org/inlineXBRL/transformation/2015-02-26"\r\n'
 'xmlns:tifrs-SCF="http://www.xbrl.org/tifrs/scf/2020-06-30"\r\n'
 'xmlns:tifrs-ar="http://www.xbrl.org/tifrs/ar/2020-06-30"\r\n'
 'xmlns:tifrs-bsci-ci="http://www.xbrl.org/tifrs/bsci/ci/2020-06-30"\r\n'
 'xmlns:tifrs-es="http://www.xbrl.org/tifrs/es/2020-06-30"\r\n'
 'xmlns:tifr

In [3]:
# 將網頁編碼轉為Big5字碼
response.encoding = "big5"

# 轉為bs4格式
soup = BeautifulSoup(response.text, 'html.parser')

In [4]:
pprint(soup)

<html>
<head>
<meta content="text/html; charset=utf-8" http-equiv="Content-Type"/>
<?xml version="1.0" encoding="UTF-8"?>
<html xmlns="http://www.w3.org/1999/xhtml" xmlns:ifrs-full="http://xbrl.ifrs.org/taxonomy/2017-03-09/ifrs-full" xmlns:iso4217="http://www.xbrl.org/2003/iso4217" xmlns:ix="http://www.xbrl.org/2013/inlineXBRL" xmlns:ixt="http://www.xbrl.org/inlineXBRL/transformation/2015-02-26" xmlns:link="http://www.xbrl.org/2003/linkbase" xmlns:tifrs-ar="http://www.xbrl.org/tifrs/ar/2020-06-30" xmlns:tifrs-bsci-ci="http://www.xbrl.org/tifrs/bsci/ci/2020-06-30" xmlns:tifrs-es="http://www.xbrl.org/tifrs/es/2020-06-30" xmlns:tifrs-notes="http://www.xbrl.org/tifrs/notes/2020-06-30" xmlns:tifrs-scf="http://www.xbrl.org/tifrs/scf/2020-06-30" xmlns:xbrldi="http://xbrl.org/2006/xbrldi" xmlns:xbrldt="http://xbrl.org/2005/xbrldt" xmlns:xbrli="http://www.xbrl.org/2003/instance" xmlns:xlink="http://www.w3.org/1999/xlink">
<head>
<meta content="text/html; charset=utf-8" http-equiv="Content-Type"

In [5]:
# 查詢財報資料
tables = soup.find_all("table")

In [6]:
tables[0]

<table style="width:90%">
<tr><th colspan="5"><span class="zh">資產負債表</span><span class="en">Balance Sheet</span></th></tr>
<tr>
<th><span class="zh">代號</span><span class="en">Code</span></th>
<th><span class="zh">會計項目</span><span class="en">Accounting Title</span></th>
<th><span class="zh">2025年9月30日</span><span class="en">2025/9/30</span></th>
<th><span class="zh">2024年12月31日</span><span class="en">2024/12/31</span></th>
<th><span class="zh">2024年9月30日</span><span class="en">2024/9/30</span></th>
</tr>
<tr>
<td style="text-align:center"></td>
<td><span class="zh">資產</span><span class="en">Assets</span></td>
<td class="amt"></td>
<td class="amt"></td>
<td class="amt"></td>
</tr>
<tr>
<td style="text-align:center"></td>
<td><span class="zh">　流動資產</span><span class="en">　Current assets</span></td>
<td class="amt"></td>
<td class="amt"></td>
<td class="amt"></td>
</tr>
<tr>
<td style="text-align:center">1100</td>
<td><span class="zh">　　現金及約當現金</span><span class="en">　　Cash and cash equiva

In [7]:
# 資料彙整 
def parse_financial_table(table):

    rows = []
    for tr in table.find_all("tr"):
        cols = tr.find_all(["td", "th"])
        row = []

        for td in cols:
            # 中文優先，如果沒有中文，就用英文
            zh = td.find("span", class_="zh")
            en = td.find("span", class_="en")

            # 數值欄：抓 ix:nonfraction
            ix = td.find("ix:nonfraction")

            if ix:
                # 數值中的括號 (xxxx) 表示負數
                raw_val = ix.text.strip()

                raw_val = raw_val.replace(",", "")  # 移除千分號
                if raw_val.startswith("(") and raw_val.endswith(")"):
                    raw_val = "-" + raw_val[1:-1]   # (123) → -123

                row.append(raw_val)
            else:
                # 不是數字欄 → 抓文字
                if zh:
                    row.append(zh.text.strip())
                elif en:
                    row.append(en.text.strip())
                else:
                    row.append(td.text.strip())

        rows.append(row)

    # 轉成 DataFrame
    df = pd.DataFrame(rows)

    return df

In [8]:
# 0: 資產負債表
# 1: 綜合損益表
# 2: 現金流量表
# 3: 當期權益變動表
# 4: 去年同期權益變動表
# 5: 會計師查核（核閱）報告
# 6: 公司沿革及業務範圍
# 7: 通過財報之日期及程序
# ...請自行發揮

selectNum = 0

parse_financial_table(tables[selectNum])

0                          1           2            3           4
0   資產負債表                       None        None         None        None
1      代號                       會計項目  2025年9月30日  2024年12月31日  2024年9月30日
2                                 資產                                     
3                               流動資產                                     
4    1100                    現金及約當現金    87297723     77764504    74379277
..    ...                        ...         ...          ...         ...
84   36XX                      非控制權益    57096805     59810770    56473777
85   3XXX                       權益總額   280567870    307908264   303383722
86   3X2X                    負債及權益總計   581076431    593413647   586487539
87   3998          預收股款（權益項下）之約當發行股數           0            0           0
88   3999  母公司暨子公司所持有之母公司庫藏股股數（單位：股）    58000000     20000000    20000000

[89 rows x 5 columns]